In [3]:
import os
import datetime
import warnings
import polars as pl
import pandas as pd
import altair as alt

from src.najdi_rok import najdi_rok
from src.pocet_stran import pocet_stran
from src.bez_bordelu import bez_bordelu
from src.alt_friendly import alt_friendly
from src.hezke_jmeno import hezke_jmeno
from src.kristi_promin import kristi_promin
from src.zjisti_vazbu import zjisti_vazbu
from src.me_to_neurazi import me_to_neurazi

pl.Config(tbl_rows=100)
alt.data_transformers.disable_max_rows()
alt.themes.register('irozhlas', kristi_promin)
alt.themes.enable('irozhlas')
warnings.filterwarnings('ignore')

In [4]:
df = pl.read_parquet(os.path.join("data/cnb_sloupce","leader.parquet"))
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","100.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","008.parquet")), left_on="001", right_on="001", how="left")
df = df.to_pandas()
df = df[df["leader"].str[6].isin(["a", "t"])]
df = df[~df["leader"].str[7].isin(["b", "i", "s", " "])]
df = df[(df["008"].str[15:17] == "xr") & (df["008"].str[35:38] == "cze")]
df = pl.from_pandas(df)
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","020.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","022.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","245.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","300.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","655.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","700.parquet")), left_on="001", right_on="001", how="left")
df = df.explode("022_a").filter(pl.col("022_a").is_null())
df = df.with_columns(pl.col('008').map_elements(najdi_rok, return_dtype=int).alias('rok'))
df = df.with_columns(pl.col('300_a').map_elements(pocet_stran, return_dtype=int).alias('stran'))
df = df.with_columns(pl.col('245_a').map_elements(bez_bordelu, return_dtype=str))
df = df.explode("020_q").with_columns(pl.col("020_q").map_elements(zjisti_vazbu, return_dtype=str).alias('vazba'))
df = df.explode('245_p').with_columns(pl.col('245_p').map_elements(bez_bordelu, return_dtype=str))
print(len(df))
df = df.filter(~pl.col('rok').is_null()).sort(by='rok')
df = df.filter((~pl.col("245_h").str.contains("grafika")) | pl.col("245_h").is_null())
print(len(df))

1001279
991612


In [5]:
df = df.filter(pl.col("rok") >= 1800)

In [6]:
df.group_by(["100_a","100_7"]).len().sort(by="len",descending=True).head(n=100)

shape: (100, 3)
┌─────────────────────────────────┬───────────────┬────────┐
│ 100_a                           ┆ 100_7         ┆ len    │
│ ---                             ┆ ---           ┆ ---    │
│ str                             ┆ str           ┆ u32    │
╞═════════════════════════════════╪═══════════════╪════════╡
│ null                            ┆ null          ┆ 202742 │
│ Unger, Gert F.,                 ┆ jn20001103529 ┆ 1682   │
│ Vandenberg, Patricia,           ┆ jn20000810141 ┆ 1185   │
│ Němcová, Božena,                ┆ jk01083016    ┆ 1126   │
│ Jirásek, Alois,                 ┆ jk01051816    ┆ 1112   │
│ Čapek, Karel,                   ┆ jk01021023    ┆ 874    │
│ Shakespeare, William,           ┆ jn19981002129 ┆ 822    │
│ Verne, Jules,                   ┆ jn19990008769 ┆ 793    │
│ Dark, Jason,                    ┆ jn20000810032 ┆ 725    │
│ Vedral, Jiří,                   ┆ mzk2003169026 ┆ 713    │
│ Javořická, Vlasta,              ┆ jk01051344    ┆ 685    │
│ Neruda, Jan,                    ┆ jk01083209    ┆ 666    │
│ Courths-Mahler, Hedwig,         ┆ jn19990001513 ┆ 652    │
│ May, Karl,                      ┆ jn19990005499 ┆ 573    │
│ Kirby, John                     ┆ jx20040611003 ┆ 563    │
│ Erben, Karel Jaromír,           ┆ jk01030532    ┆ 543    │
│ Vrchlický, Jaroslav,            ┆ jk01151037    ┆ 533    │
│ Masaryk, Tomáš Garrigue,        ┆ jk01080472    ┆ 499    │
│ Dumas, Alexandre,               ┆ jn19990001907 ┆ 432    │
│ Rais, Karel Václav,             ┆ jk01101955    ┆ 407    │
│ Tyl, Josef Kajetán,             ┆ jk01140553    ┆ 405    │
│ Tolstoj, Lev Nikolajevič,       ┆ jn19981002230 ┆ 398    │
│ Komenský, Jan Amos,             ┆ jk01061444    ┆ 391    │
│ Čech, Svatopluk,                ┆ jk01021137    ┆ 388    │
│ Štohl, Pavel,                   ┆ xx0024514     ┆ 380    │
│ Mácha, Karel Hynek,             ┆ jk01072915    ┆ 377    │
│ Lada, Josef,                    ┆ jk01071364    ┆ 377    │
│ Clifton, Léon                   ┆ xx0111518     ┆ 353    │
│ Zeyer, Julius,                  ┆ jk01152552    ┆ 352    │
│ Nedbalová, Marie                ┆ jo2014816080  ┆ 345    │
│ Pittnerová, Vlasta,             ┆ jk01093291    ┆ 342    │
│ Seifert, Jaroslav,              ┆ jk01110657    ┆ 340    │
│ Lenin, Vladimir Il‘jič,         ┆ jn19981001737 ┆ 340    │
│ Strong, Pitt,                   ┆ jo2005267810  ┆ 324    │
│ Batěk, Alexandr,                ┆ jk01011106    ┆ 323    │
│ Světlá, Karolina,               ┆ jk01121895    ┆ 323    │
│ Novotný, Miloš                  ┆ mzk2013757672 ┆ 320    │
│ Birkner-Mahler, Frieda,         ┆ jn20000600873 ┆ 319    │
│ Scott, William,                 ┆ ola2003188680 ┆ 318    │
│ Žáček, Jiří,                    ┆ jk01152946    ┆ 317    │
│ Šváb-Malostranský, Josef,       ┆ jk01131780    ┆ 315    │
│ Hrubín, František,              ┆ jk01042920    ┆ 313    │
│ Baar, Jindřich Šimon,           ┆ jk01010468    ┆ 311    │
│ Grey, Zane,                     ┆ jn19990002874 ┆ 306    │
│ Christie, Agatha,               ┆ jn19981000482 ┆ 298    │
│ Havlíček Borovský, Karel,       ┆ jk01040361    ┆ 298    │
│ Foglar, Jaroslav,               ┆ jk01031485    ┆ 289    │
│ Machar, Josef Svatopluk,        ┆ jk01072996    ┆ 288    │
│ Miler, Zdeněk,                  ┆ jk01081695    ┆ 286    │
│ Pospíšilová, Zuzana,            ┆ mzk2006331486 ┆ 284    │
│ Beneš Třebízský, Václav,        ┆ jk01011653    ┆ 282    │
│ Hálek, Vítězslav,               ┆ jk01033219    ┆ 282    │
│ Brezina, Thomas,                ┆ jn20001227589 ┆ 280    │
│ Nezval, Vítězslav,              ┆ jk01090162    ┆ 279    │
│ Dostojevskij, Fedor Michajlovi… ┆ jn19990210182 ┆ 278    │
│ David, Petr,                    ┆ xx0006786     ┆ 277    │
│ Steiner, Rudolf,                ┆ jn19990009728 ┆ 277    │
│ Brahová, Marie                  ┆ jn20010310261 ┆ 273    │
│ Wallace, Edgar,                 ┆ jn19990008883 ┆ 272    │
│ Vrba, Jan,                      ┆ jk01150966    ┆ 271    │
│ Šulc, Petr,      

In [7]:
nechcemejetam = [
    "jn19990008769",
    "jx20060515016",
    "jn19981002230",
    "jn19981001737",
    "jn19990210182",
    "jn19990001842",
    "jn19990002786",
    "jn19990004346",
    "jn20020721077",
    "jn19990210513",
    "jn19990005488",
    "jo20000080627",
    "jn19990000171",
    "jn20001005715",
    "jn19981002409",
    "jn20000810141",
    "jn19981002129",
    "jn20001103529",
    "jn20000810032",
    "jn19990001513",
    "jx20040611003",
    "jn19990005499",
    "jn19981002230",
    "jn19990001907",
    "jo2005267810",
    "jo20241218643"
]

In [8]:
df = df.filter(~pl.col("100_7").is_in(nechcemejetam))

In [9]:
df.group_by("rok").len().sort(by="rok")

shape: (226, 2)
┌──────┬───────┐
│ rok  ┆ len   │
│ ---  ┆ ---   │
│ i64  ┆ u32   │
╞══════╪═══════╡
│ 1800 ┆ 1     │
│ 1801 ┆ 10    │
│ 1802 ┆ 10    │
│ 1803 ┆ 14    │
│ 1804 ┆ 15    │
│ 1805 ┆ 16    │
│ 1806 ┆ 9     │
│ 1807 ┆ 16    │
│ 1808 ┆ 16    │
│ 1809 ┆ 14    │
│ 1810 ┆ 15    │
│ 1811 ┆ 10    │
│ 1812 ┆ 20    │
│ 1813 ┆ 14    │
│ 1814 ┆ 19    │
│ 1815 ┆ 20    │
│ 1816 ┆ 21    │
│ 1817 ┆ 21    │
│ 1818 ┆ 35    │
│ 1819 ┆ 38    │
│ 1820 ┆ 40    │
│ 1821 ┆ 49    │
│ 1822 ┆ 40    │
│ 1823 ┆ 42    │
│ 1824 ┆ 45    │
│ 1825 ┆ 50    │
│ 1826 ┆ 33    │
│ 1827 ┆ 45    │
│ 1828 ┆ 42    │
│ 1829 ┆ 32    │
│ 1830 ┆ 48    │
│ 1831 ┆ 47    │
│ 1832 ┆ 34    │
│ 1833 ┆ 33    │
│ 1834 ┆ 32    │
│ 1835 ┆ 45    │
│ 1836 ┆ 45    │
│ 1837 ┆ 37    │
│ 1838 ┆ 37    │
│ 1839 ┆ 38    │
│ 1840 ┆ 68    │
│ 1841 ┆ 49    │
│ 1842 ┆ 63    │
│ 1843 ┆ 75    │
│ 1844 ┆ 98    │
│ 1845 ┆ 76    │
│ 1846 ┆ 82    │
│ 1847 ┆ 90    │
│ 1848 ┆ 99    │
│ 1849 ┆ 104   │
│ …    ┆ …     │
│ 1976 ┆ 3795  │
│ 1977 ┆ 3783  │
│ 1978 ┆ 3770  │
│ 1979 ┆ 4010  │
│ 1980 ┆ 4118  │
│ 1981 ┆ 3913  │
│ 1982 ┆ 4014  │
│ 1983 ┆ 3985  │
│ 1984 ┆ 4158  │
│ 1985 ┆ 3994  │
│ 1986 ┆ 4209  │
│ 1987 ┆ 4267  │
│ 1988 ┆ 4349  │
│ 1989 ┆ 4690  │
│ 1990 ┆ 5215  │
│ 1991 ┆ 5821  │
│ 1992 ┆ 6441  │
│ 1993 ┆ 7277  │
│ 1994 ┆ 7642  │
│ 1995 ┆ 8577  │
│ 1996 ┆ 9625  │
│ 1997 ┆ 10220 │
│ 1998 ┆ 10555 │
│ 1999 ┆ 10836 │
│ 2000 ┆ 11939 │
│ 2001 ┆ 11733 │
│ 2002 ┆ 12151 │
│ 2003 ┆ 12578 │
│ 2004 ┆ 13100 │
│ 2005 ┆ 13708 │
│ 2006 ┆ 14439 │
│ 2007 ┆ 14846 │
│ 2008 ┆ 15559 │
│ 2009 ┆ 14674 │
│ 2010 ┆ 15122 │
│ 2011 ┆ 14886 │
│ 2012 ┆ 14889 │
│ 2013 ┆ 14808 │
│ 2014 ┆ 15089 │
│ 2015 ┆ 15489 │
│ 2016 ┆ 14653 │
│ 2017 ┆ 14434 │
│ 2018 ┆ 14548 │
│ 2019 ┆ 14153 │
│ 2020 ┆ 12872 │
│ 2021 ┆ 13166 │
│ 2022 ┆ 13551 │
│ 2023 ┆ 12045 │
│ 2024 ┆ 10424 │
│ 2025 ┆ 440   │
└──────┴───────┘

In [10]:
df.group_by("100_a").len().sort(by="len",descending=True).head(100)

shape: (100, 2)
┌─────────────────────────────┬──────┐
│ 100_a                       ┆ len  │
│ ---                         ┆ ---  │
│ str                         ┆ u32  │
╞═════════════════════════════╪══════╡
│ Němcová, Božena,            ┆ 1126 │
│ Jirásek, Alois,             ┆ 1112 │
│ Čapek, Karel,               ┆ 880  │
│ Vedral, Jiří,               ┆ 714  │
│ Javořická, Vlasta,          ┆ 685  │
│ Neruda, Jan,                ┆ 666  │
│ Erben, Karel Jaromír,       ┆ 543  │
│ Vrchlický, Jaroslav,        ┆ 533  │
│ Masaryk, Tomáš Garrigue,    ┆ 499  │
│ Rais, Karel Václav,         ┆ 407  │
│ Tyl, Josef Kajetán,         ┆ 405  │
│ Čech, Svatopluk,            ┆ 396  │
│ Komenský, Jan Amos,         ┆ 391  │
│ Štohl, Pavel,               ┆ 380  │
│ Lada, Josef,                ┆ 378  │
│ Mácha, Karel Hynek,         ┆ 377  │
│ Clifton, Léon               ┆ 353  │
│ Zeyer, Julius,              ┆ 352  │
│ Nedbalová, Marie            ┆ 345  │
│ Pittnerová, Vlasta,         ┆ 342  │
│ Seifert, Jaroslav,          ┆ 340  │
│ Batěk, Alexandr,            ┆ 323  │
│ Světlá, Karolina,           ┆ 323  │
│ Novotný, Miloš              ┆ 320  │
│ Birkner-Mahler, Frieda,     ┆ 319  │
│ Scott, William,             ┆ 318  │
│ Žáček, Jiří,                ┆ 317  │
│ Šváb-Malostranský, Josef,   ┆ 315  │
│ Hrubín, František,          ┆ 313  │
│ Baar, Jindřich Šimon,       ┆ 311  │
│ Grey, Zane,                 ┆ 306  │
│ Havlíček Borovský, Karel,   ┆ 298  │
│ Christie, Agatha,           ┆ 298  │
│ Hálek, Vítězslav,           ┆ 293  │
│ David, Petr,                ┆ 292  │
│ Foglar, Jaroslav,           ┆ 289  │
│ Machar, Josef Svatopluk,    ┆ 288  │
│ Vrba, Jan,                  ┆ 287  │
│ Miler, Zdeněk,              ┆ 286  │
│ Pospíšilová, Zuzana,        ┆ 284  │
│ Beneš Třebízský, Václav,    ┆ 282  │
│ Šulc, Petr,                 ┆ 280  │
│ Brezina, Thomas,            ┆ 280  │
│ Nezval, Vítězslav,          ┆ 279  │
│ Steiner, Rudolf,            ┆ 277  │
│ Brahová, Marie              ┆ 273  │
│ Wallace, Edgar,             ┆ 272  │
│ Bezruč, Petr,               ┆ 270  │
│ Cílek, Roman,               ┆ 268  │
│ London, Jack,               ┆ 268  │
│ Gardner, Erle Stanley,      ┆ 265  │
│ Březinová, Ivona,           ┆ 264  │
│ Rowling, J. K.,             ┆ 263  │
│ Herrmann, Ignát,            ┆ 261  │
│ Doležalová, Alena Bára      ┆ 261  │
│ Hašek, Jaroslav,            ┆ 260  │
│ Nejedlý, Zdeněk,            ┆ 259  │
│ Štiková, Věra               ┆ 256  │
│ Petiška, Eduard,            ┆ 254  │
│ Majerová, Marie,            ┆ 253  │
│ Dobrovolný, Bohumil,        ┆ 251  │
│ Steel, Danielle,            ┆ 249  │
│ Balzac, Honoré de,          ┆ 248  │
│ Šplíchal, Antonín,          ┆ 245  │
│ Klostermann, Karel,         ┆ 244  │
│ Bauer, Jan,                 ┆ 242  │
│ Klínský, Petr               ┆ 241  │
│ Svoboda, F. X.,             ┆ 240  │
│ Vondruška, Vlastimil,       ┆ 235  │
│ Čtvrtek, Václav,            ┆ 232  │
│ Maruna, Jan,                ┆ 230  │
│ Čechov, Anton Pavlovič,     ┆ 225  │
│ Šťastný, Alfons Bohumil,    ┆ 225  │
│ McBain, Ed,                 ┆ 224  │
│ Štíplová, Ljuba,            ┆ 224  │
│ Sedláček, Václav,           ┆ 223  │
│ Zahradník-Brodský, Bohumil, ┆ 223  │
│ Hrabal, Bohumil,            ┆ 222  │
│ Etzold, Hans-Rüdiger,       ┆ 219  │
│ Deml, Jakub,                ┆ 217  │
│ Říha, Bohumil,              ┆ 217  │
│ Poláček, Karel,             ┆ 216  │
│ Čapek, Josef,               ┆ 216  │
│ Kříženecký, Jaroslav,       ┆ 216  │
│ Balák, Karel,               ┆ 215  │
│ Bass, Eduard,               ┆ 213  │
│ Zola, Émile,                ┆ 212  │
│ Kožík, František,           ┆ 210  │
│ Sekora, Ondřej,             ┆ 206  │
│ Durych, Jaroslav,           ┆ 206  │
│ Schelle, Karel,             ┆ 205  │
│ Vančura, Vladislav,         ┆ 204  │
│ Suchý, Jiří,                ┆ 202  │
│ Rolland, Romain,            ┆ 202  │
│ Čečetka, František Josef,   ┆ 201  │
│ Caha, Arnošt,               ┆ 201  │
│ Vymazal, František,         ┆ 200  │
│ Švan

In [11]:
df.filter(pl.col("100_a") == "Mark, William,")

shape: (0, 73)
┌────────┬─────┬──────────┬───────┬───┬───────────┬─────┬───────┬───────┐
│ leader ┆ 001 ┆ 100_ind1 ┆ 100_a ┆ … ┆ 700_g     ┆ rok ┆ stran ┆ vazba │
│ ---    ┆ --- ┆ ---      ┆ ---   ┆   ┆ ---       ┆ --- ┆ ---   ┆ ---   │
│ str    ┆ str ┆ str      ┆ str   ┆   ┆ list[str] ┆ i64 ┆ i64   ┆ str   │
╞════════╪═════╪══════════╪═══════╪═══╪═══════════╪═════╪═══════╪═══════╡
└────────┴─────┴──────────┴───────┴───┴───────────┴─────┴───────┴───────┘

In [12]:
len(df)

728131

In [13]:
df = df.explode("100_4").filter(pl.col("100_4") == "aut")

In [14]:
len(df)

691262

In [15]:
df = df.unique(subset=["100_a","245_a"])

In [16]:
len(df)

485690

In [17]:
len(list(set(df.select(pl.col("100_7")).to_series().to_list())))

147909

In [18]:
df = df.with_columns(pl.col("100_a").map_elements(hezke_jmeno).alias("jméno"))

In [19]:
df.group_by("jméno").len().sort(by="len",descending=True).head(11)

shape: (11, 2)
┌─────────────────────────┬─────┐
│ jméno                   ┆ len │
│ ---                     ┆ --- │
│ str                     ┆ u32 │
╞═════════════════════════╪═════╡
│ Jiří Vedral             ┆ 656 │
│ Božena Němcová          ┆ 274 │
│ Alexandr Batěk          ┆ 261 │
│ Josef Šváb-Malostranský ┆ 260 │
│ Jan Amos Komenský       ┆ 258 │
│ Zuzana Pospíšilová      ┆ 249 │
│ Jan Neruda              ┆ 236 │
│ Jaroslav Vrchlický      ┆ 233 │
│ Tomáš Garrigue Masaryk  ┆ 209 │
│ Alfons Bohumil Šťastný  ┆ 205 │
│ Rudolf Steiner          ┆ 201 │
└─────────────────────────┴─────┘

In [20]:
hvezdy = df.group_by("100_7").len().sort(by="len",descending=True).head(10).select(pl.col("100_7")).to_series().to_list()
hvezdy

['mzk2003169026',
 'jk01083016',
 'jk01011106',
 'jk01131780',
 'jk01061444',
 'mzk2006331486',
 'jk01083209',
 'jk01151037',
 'jk01080472',
 'jk01131099']

In [21]:
import datetime

In [22]:
aut = pl.read_parquet(os.path.join("data","aut_vyber.parquet"))

In [23]:
mrtvi = aut.explode("100_7").filter(pl.col("100_7").is_in(hvezdy)).explode("046_g").with_columns(pl.col("046_g").map_elements(lambda x: int(x)).alias("umrti")).select(pl.col(["100_7","umrti"])).filter(pl.col('umrti').is_between(1800,2025)).with_columns(pl.col("umrti").map_elements(lambda x: datetime.date(year=int(x), month=1, day=1), return_dtype=pl.Date).cast(pl.Datetime))

In [24]:
do_grafu = df.filter(
    pl.col("100_7").is_in(hvezdy)
).with_columns(
    pl.col("rok").map_elements(lambda x: datetime.date(year=int(x), month=1, day=1), return_dtype=pl.Date).cast(pl.Datetime)
).join(
    df.group_by('100_7').len(), on='100_7', how='left'
).filter(
    pl.col("len") > 10
).with_columns(
    pl.col("len").map_elements(lambda x: str(x) + "×")
).join(
    mrtvi, how='left', on='100_7'
).with_columns(
    pl.concat_str([pl.col('len'), pl.col('jméno')], separator=' ').alias('jméno')
)

In [25]:
do_grafu

shape: (2_840, 76)
┌────────────────┬────────────────┬──────────┬────────────────┬───┬───────────┬────────────────┬──────┬────────────────┐
│ leader         ┆ 001            ┆ 100_ind1 ┆ 100_a          ┆ … ┆ vazba     ┆ jméno          ┆ len  ┆ umrti          │
│ ---            ┆ ---            ┆ ---      ┆ ---            ┆   ┆ ---       ┆ ---            ┆ ---  ┆ ---            │
│ str            ┆ str            ┆ str      ┆ str            ┆   ┆ str       ┆ str            ┆ str  ┆ datetime[μs]   │
╞════════════════╪════════════════╪══════════╪════════════════╪═══╪═══════════╪════════════════╪══════╪════════════════╡
│ nam a22     1  ┆ bk192903271    ┆ 1        ┆ Němcová,       ┆ … ┆ null      ┆ 274× Božena    ┆ 274× ┆ 1862-01-01     │
│ 4500           ┆                ┆          ┆ Božena,        ┆   ┆           ┆ Němcová        ┆      ┆ 00:00:00       │
│ nam a22      a ┆ bknmik04838    ┆ 1        ┆ Komenský, Jan  ┆ … ┆ brožovaná ┆ 258× Jan Amos  ┆ 258× ┆ null           │
│ 4500           ┆                ┆          ┆ Amos,          ┆   ┆           ┆ Komenský       ┆      ┆                │
│ nam a22        ┆ cpk20041191504 ┆ 1        ┆ Vedral, Jiří,  ┆ … ┆ brožovaná ┆ 655× Jiří      ┆ 655× ┆ null           │
│ aa4500         ┆                ┆          ┆                ┆   ┆           ┆ Vedral         ┆      ┆                │
│ nam a22     1  ┆ nos190248589   ┆ 1        ┆ Šťastný,       ┆ … ┆ brožovaná ┆ 205× Alfons    ┆ 205× ┆ 1922-01-01     │
│ 4500           ┆                ┆          ┆ Alfons         ┆   ┆           ┆ Bohumil        ┆      ┆ 00:00:00       │
│                ┆                ┆          ┆ Bohumil,       ┆   ┆           ┆ Šťastný        ┆      ┆                │
│ nam a22      a ┆ np9542515      ┆ 1        ┆ Masaryk, Tomáš ┆ … ┆ pevná     ┆ 209× Tomáš     ┆ 209× ┆ 1937-01-01     │
│ 4500           ┆                ┆          ┆ Garrigue,      ┆   ┆           ┆ Garrigue       ┆      ┆ 00:00:00       │
│                ┆                ┆          ┆                ┆   ┆           ┆ Masaryk        ┆      ┆                │
│ cam a22      a ┆ nkc20142611690 ┆ 1        ┆ Vedral, Jiří,  ┆ … ┆ brožovaná ┆ 655× Jiří      ┆ 655× ┆ null           │
│ 4500           ┆                ┆          ┆                ┆   ┆           ┆ Vedral         ┆      ┆                │
│ nam a22     1  ┆ nos190254839   ┆ 1        ┆ Vrchlický,     ┆ … ┆ null      ┆ 233× Jaroslav  ┆ 233× ┆ 1912-01-01     │
│ 4500           ┆                ┆          ┆ Jaroslav,      ┆   ┆           ┆ Vrchlický      ┆      ┆ 00:00:00       │
│ cam a22      i ┆ nkc20142636527 ┆ 1        ┆ Vedral, Jiří,  ┆ … ┆ null      ┆ 655× Jiří      ┆ 655× ┆ null           │
│ 4500           ┆                ┆          ┆                ┆   ┆           ┆ Vedral         ┆      ┆                │
│ nam a22     1  ┆ nos190131992   ┆ 1        ┆ Němcová,       ┆ … ┆ brožovaná ┆ 274× Božena    ┆ 274× ┆ 1862-01-01     │
│ a4500          ┆                ┆          ┆ Božena,        ┆   ┆           ┆ Němcová        ┆      ┆ 00:00:00       │
│ nam a22     1  ┆ bk196001828    ┆ 1        ┆ Němcová,       ┆ … ┆ null      ┆ 274× Božena    ┆ 274× ┆ 1862-01-01     │
│ 4500           ┆                ┆          ┆ Božena,        ┆   ┆           ┆ Němcová        ┆      ┆ 00:00:00       │
│ cam a22      i ┆ nkc20142636442 ┆ 1        ┆ Vedral, Jiří,  ┆ … ┆ null      ┆ 655× Jiří      ┆ 655× ┆ null           │
│ 4500           ┆                ┆          ┆                ┆   ┆           ┆ Vedral         ┆      ┆                │
│ nam a22      a ┆ nkc20051574955 ┆ 1        ┆ Vedral, Jiří,  ┆ … ┆ brožovaná ┆ 655× Jiří      ┆ 655× ┆ null           │
│ 4500           ┆                ┆          ┆                ┆   ┆           ┆ Vedral         ┆      ┆                │
│ nam a22      i ┆ srk19960122569 ┆ 1        ┆ Masaryk, Tomáš ┆ … ┆ pevná     ┆ 209× Tomáš     ┆ 209× ┆ 1937-01-01     │
│ 4500           ┆                ┆          ┆ Garrigue,      ┆   ┆           ┆ Garrigue       ┆      ┆ 00:00

In [26]:
hvezdy_poradi = do_grafu.group_by('jméno').len().sort(by="len",descending=True).to_series().to_list()
hvezdy_poradi

['655× Jiří Vedral',
 '274× Božena Němcová',
 '261× Alexandr Batěk',
 '260× Josef Šváb-Malostranský',
 '258× Jan Amos Komenský',
 '249× Zuzana Pospíšilová',
 '236× Jan Neruda',
 '233× Jaroslav Vrchlický',
 '209× Tomáš Garrigue Masaryk',
 '205× Alfons Bohumil Šťastný']

In [27]:
y_encoding = {
        'field': 'jméno',
        'type': 'nominal',
        'title': None,
        'sort': hvezdy
    }

In [28]:
len(do_grafu)

2840

In [29]:
do_grafu.filter(pl.col("jméno") == "Božena Němcová").group_by("245_a").len()

shape: (0, 2)
┌───────┬─────┐
│ 245_a ┆ len │
│ ---   ┆ --- │
│ str   ┆ u32 │
╞═══════╪═════╡
└───────┴─────┘

In [31]:
import json
from src.me_to_neurazi import me_to_neurazi
with open(os.path.join('src','kredity.json'), 'r', encoding='utf-8') as kredity:
    kredity = json.loads(kredity.read())

In [39]:
base = alt.Chart(do_grafu.to_pandas(), 
                     title=alt.Title(f"{len(hvezdy)} nejvydávanějších autorů a autorek",
                                     subtitle=["Co tečka, to kniha. Černá čárka označuje rok úmrtí.","Graf nezobrazuje reprinty s opakovaným názvem."]))

kulicky = base.mark_circle(size=6).encode(
            x=alt.X("rok:T", title=None, axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6', tickCount=5)), 
            y=alt.Y("jméno:N", sort=hvezdy, title=None, axis=alt.Axis(orient='left', domainOpacity=0, tickColor='white', labelExpr='split(datum.label, "× ")[1]')), 
            yOffset=alt.YOffset("jitter:Q", scale=alt.Scale(range=[3, 15])), 
            color=alt.Color('jméno:N', scale=alt.Scale(range=['#E09DA3']), 
                            sort=hvezdy_poradi).legend(None)) \
        .transform_calculate(jitter="sqrt(-2*log(random()))*cos(2*PI*random())")

kdy_umreli = base.mark_tick(
    color='#292829',  # optional: you can specify color
    thickness=1.5,
    height=9
).encode(
    x=alt.X('umrti:T', title=None),
    y=alt.Y("jméno:N", sort=hvezdy_poradi, title=None, axis=alt.Axis(orient='left', tickColor='white', labels=False)))

pocty = base.mark_circle(size=0).encode(x=alt.X('rok:T', title=None), 
    y=alt.Y('jméno:N', title=None, sort=hvezdy_poradi, axis=alt.Axis(orient="right", tickColor='white', labelExpr='split(datum.label, " ")[0]')))

zebricek = alt.layer(kulicky, pocty, kdy_umreli).properties(
    width=kredity['sirka'],
    autosize={'type': 'fit', 'contains': 'padding'}
).configure_view(stroke='transparent')

zebricek

alt.LayerChart(...)

In [41]:
me_to_neurazi(zebricek, kredity=kredity['default'], soubor="02_nejvydavanejsi_autorstvo")

<figure>
    <a href="https://data.irozhlas.cz/knihy-grafy/02_nejvydavanejsi_autorstvo.svg" target="_blank">
    <img src="https://data.irozhlas.cz/knihy-grafy/02_nejvydavanejsi_autorstvo.svg" width="100%" alt="Omlouváme se, ale alternativní text se nepodařilo vygenerovat. Texty v grafu by měly být čitelné ze zdrojového souboru SVG." />
    </a>
    </figure>


In [43]:
df.filter(pl.col("100_a") == "Pospíšilová, Zuzana,").group_by('rok').len().sort(by='rok')

shape: (21, 2)
┌──────┬─────┐
│ rok  ┆ len │
│ ---  ┆ --- │
│ i64  ┆ u32 │
╞══════╪═════╡
│ 2005 ┆ 2   │
│ 2006 ┆ 7   │
│ 2007 ┆ 7   │
│ 2008 ┆ 12  │
│ 2009 ┆ 12  │
│ 2010 ┆ 19  │
│ 2011 ┆ 20  │
│ 2012 ┆ 24  │
│ 2013 ┆ 11  │
│ 2014 ┆ 22  │
│ 2015 ┆ 12  │
│ 2016 ┆ 12  │
│ 2017 ┆ 17  │
│ 2018 ┆ 16  │
│ 2019 ┆ 10  │
│ 2020 ┆ 16  │
│ 2021 ┆ 5   │
│ 2022 ┆ 9   │
│ 2023 ┆ 6   │
│ 2024 ┆ 9   │
│ 2025 ┆ 1   │
└──────┴─────┘

In [44]:
df.filter(pl.col("100_a") == "Pospíšilová, Zuzana,").group_by('rok').len().sort(by='rok').filter(pl.col("rok").is_between(2019,2024)).select(pl.col("len")).median()

shape: (1, 1)
┌─────┐
│ len │
│ --- │
│ f64 │
╞═════╡
│ 9.0 │
└─────┘

In [45]:
(308-253)/9

6.111111111111111

In [46]:
df.filter(pl.col("100_a") == "Pospíšilová, Zuzana,").select(pl.col(['245_a','rok']))

shape: (249, 2)
┌─────────────────────────────────┬──────┐
│ 245_a                           ┆ rok  │
│ ---                             ┆ ---  │
│ str                             ┆ i64  │
╞═════════════════════════════════╪══════╡
│ Psí hrdina                      ┆ 2018 │
│ Pohádky                         ┆ 2017 │
│ Pohádky z parkoviště            ┆ 2013 │
│ Případ: detektivové             ┆ 2012 │
│ O ježkovi ze zahrádky           ┆ 2010 │
│ Hrajeme si s Géňou a-- s geome… ┆ 2010 │
│ Národní pohádky                 ┆ 2017 │
│ Pohádky před spaním             ┆ 2007 │
│ Hádanky pro školáky             ┆ 2017 │
│ O šnečkovi ze zahrádky          ┆ 2018 │
│ Matěj a stegosaurus             ┆ 2014 │
│ Kouzelné sedlo                  ┆ 2017 │
│ Mokré pohádky                   ┆ 2013 │
│ Pohádkové uspávanky             ┆ 2016 │
│ Kdo tu troubí, houká, vrčí?     ┆ 2010 │
│ Hádanky a hříčky nejen se slov… ┆ 2006 │
│ Prázdniny v talíři              ┆ 2016 │
│ Kdo a co je ve škole            ┆ 2020 │
│ Prvňáci mají rádi legraci       ┆ 2024 │
│ Skutečné příběhy se šťastným k… ┆ 2023 │
│ Nezbedný mýval                  ┆ 2021 │
│ Prázdniny s drakem              ┆ 2016 │
│ Vánoční Jedlička                ┆ 2023 │
│ Malý vláček                     ┆ 2007 │
│ Do lavic!                       ┆ 2015 │
│ Jak mluví zvířátka?             ┆ 2010 │
│ Veselý den                      ┆ 2011 │
│ Děti srdce                      ┆ 2019 │
│ Prázdniny s kouzelnou aktovkou  ┆ 2021 │
│ O lišce Matyldě a medvědu Šimr… ┆ 2017 │
│ Koťátko                         ┆ 2010 │
│ Štěňátko                        ┆ 2010 │
│ O beruškách a broučcích         ┆ 2008 │
│ Dinosauři                       ┆ 2006 │
│ Na statku                       ┆ 2006 │
│ Proč už kocour nemlsá           ┆ 2011 │
│ Zvířátka v ZOO                  ┆ 2006 │
│ Školnice Valerie odhalena       ┆ 2017 │
│ O zvířátkách povídání a veselé… ┆ 2009 │
│ Ptáci                           ┆ 2006 │
│ Strašidelný dům                 ┆ 2021 │
│ Školnice Valerie v podezření    ┆ 2017 │
│ Domeček pro šneka Palmáce       ┆ 2008 │
│ Sportovní pohádky               ┆ 2015 │
│ Hasičské pohádky                ┆ 2016 │
│ Školní štěně                    ┆ 2020 │
│ Ve městě                        ┆ 2006 │
│ Logohrátky                      ┆ 2018 │
│ Kouzelný pelíšek                ┆ 2020 │
│ Vláček Tomáš                    ┆ 2012 │
│ …                               ┆ …    │
│ Moje první úkoly před nástupem… ┆ 2008 │
│ Hravá škola hezkého chování     ┆ 2014 │
│ Hravá písmenková škola          ┆ 2013 │
│ Hádanky a úkoly pro sportovce … ┆ 2018 │
│ Hravá škola počítání            ┆ 2012 │
│ Kouzelná třída mezi strašidly   ┆ 2023 │
│ Hravá škola cvičení             ┆ 2014 │
│ Dopředu i pozpátku počítáme na… ┆ 2008 │
│ Kouzelná třída v muzeu          ┆ 2018 │
│ Kreslíme krok za krokem         ┆ 2008 │
│ Popelářské pohádky              ┆ 2022 │
│ Velká kniha předškoláka         ┆ 2018 │
│ Pohádky do hajan                ┆ 2014 │
│ Rozvoj dětské řeči              ┆ 2023 │
│ Moudrá sova Rozárka             ┆ 2006 │
│ Školní detektiv                 ┆ 2010 │
│ Jak se stal kozel zahradníkem   ┆ 2011 │
│ Šikovný syslík                  ┆ 2022 │
│ Pojďte si hrát na lékaře        ┆ 2012 │
│ Velký případ školního detektiv… ┆ 2014 │
│ Barevný svět                    ┆ 2014 │
│ Vystrašený zajíček              ┆ 2020 │
│ Čarodějnice Eulálie             ┆ 2010 │
│ Hasičské auto Jonáš             ┆ 2012 │
│ Povídánky s Oskarem             ┆ 2017 │
│ Malé štěňátko                   ┆ 2011 │
│ Kouzelná třída dostává vysvědč… ┆ 2025 │
│ Pohyb s říkadly pro nejmenší    ┆ 2009 │
│ Vánoční hvězda a splněná přání  ┆ 2017 │
│ O kůzlátku z chlívku            ┆ 2020 │
│ Včelka Adélka se učí protiklad… ┆ 2012 │
│ O broučcích                     ┆ 2013 │
│ Příhody veselých prvňáčků       ┆ 2019 │
│ Fánkova dobrodružství           ┆ 2011 │
│ O kachničce od rybníčka         ┆ 2010 │
│ Bezva kamarádi z 1. třídy       ┆ 2023 │
│ Hádanky ze dvorku         

In [47]:
vedral = df.filter(pl.col("100_a") == "Vedral, Jiří,").select(pl.col("245_a")).to_series().to_list()
vedral

['Anglicko-český lesnický slovník',
 'Turecko-český slovník ICF',
 'Anglicko-český slovník PRODCOM na CD',
 'Francouzsko-český slovník PRODCOM',
 'Německo-český církevní slovník',
 'Švédsko-český slovník ICF',
 'Dánsko-český slovník jmen zvířat a rostlin na CD',
 'Německo-český matematický slovník',
 'Bosensko-česká klasifikace zaměstnání (standardna klasifikacija zanimanja) ISCO 88',
 'Maďarsko-český katalog odpadů',
 'Turecko-český slovník klasifikace produkce CPA 2008',
 'Chemie pro překladatele 2.',
 'Slovinsko-český slovník PRODCOM',
 'Litevsko-český slovník PRODCOM',
 'Německo-český slovník - lékařské přístroje',
 'Arabsko-český zemědělský slovník na CD',
 'Řecko-český katalog odpadů',
 'Anglicko-český slovník jmen lichokopytníků a sudokopytníků',
 'Česko-japonský slovník jmen rostlin',
 'Turecko-český katalog odpadů',
 'Norsko-český slovník třídění odpadů',
 'Francouzsko-český slovník veřejných zakázek CPV',
 'Chorvatsko-český slovník PRODCOM',
 'Česko-thajský slovník nemocí a p

In [48]:
[x for x in vedral if "chemie" in x.lower()]

['Chemie pro překladatele 2.',
 'Chemie pro překladatele - španělština',
 'Chemie I.',
 'Chemie V.',
 'Chemie II.',
 'Chemie IV.',
 'Chemie pro překladatele - italština',
 'Chemie III.',
 'Chemie pro překladatele',
 'Chemie VI.',
 'Chemie pro překladatele - jazyky bývalé Jugoslávie']

In [49]:
[x for x in vedral if "sex" in x.lower()]

['Anglicko-český slovník sexu', 'Anglicko-český slovník sexu na CD']

In [50]:
with open(os.path.join("data_raw","vedral.json"), "w+", encoding="utf-8") as v:
    v.write(json.dumps(vedral))